# ERP Location Data Cleaning (Bronze → Silver)

This notebook prepares **`bronze.erp_loc_a101`** for the Silver layer.

Goal:
- clean customer IDs (`CID`)
- standardize country values (`CNTRY`)
- output a normalized dataset ready for analytics and joins

We follow a simple pipeline:
1. Load raw bronze table  
2. Inspect key fields  
3. Clean CID format  
4. Explore country inconsistencies  
5. Normalize country names  
6. Write final Silver table/

In [0]:
# Load bronze source
from pyspark.sql import functions as F

spark.sql("USE CATALOG datawarehouse")

df_raw = spark.table("bronze.erp_loc_a101")

df_raw.display()

CID CNTRY AW-00011000 Australia AW-00011001 Australia AW-00011002 Australia AW-00011003 Australia AW-00011004 Australia AW-00011005 Australia AW-00011006 Australia AW-00011007 Australia AW-00011008 Australia AW-00011009 Australia AW-00011010 Australia AW-00011011 Australia AW-00011012 US AW-00011013 US AW-00011014 US AW-00011015 US AW-00011016 US AW-00011017 Australia AW-00011018 Australia AW-00011019 Canada AW-00011020 Canada AW-00011021 US AW-00011022 US AW-00011023 US AW-00011024 US AW-00011025 Australia AW-00011026 Australia AW-00011027 Australia AW-00011028 Australia AW-00011029 Australia AW-00011030 Australia AW-00011031 Australia AW-00011032 Australia AW-00011033 Australia AW-00011034 Australia AW-00011035 Australia AW-00011036 US AW-00011037 Canada AW-00011038 Australia AW-00011039 Australia AW-00011040 US AW-00011041 US AW-00011042 US AW-00011043 US AW-00011044 Australia AW-00011045 Australia AW-00011046 Australia AW-00011047 Australia AW-00011048 Australia AW-00011049 US AW-00011050 Australia AW-00011051 Australia AW-00011052 Australia AW-00011053 US AW-00011054 Australia AW-00011055 Australia AW-00011056 Australia AW-00011057 Australia AW-00011058 Australia AW-00011059 Australia AW-00011060 Australia AW-00011061 Australia AW-00011062 US AW-00011063 US AW-00011064 US AW-00011065 US AW-00011066 US AW-00011067 US AW-00011068 Australia AW-00011069 Australia AW-00011070 Australia AW-00011071 Australia AW-00011072 Australia AW-00011073 Australia AW-00011074 Australia AW-00011075 Australia AW-00011076 Australia AW-00011077 Australia AW-00011078 Canada AW-00011079 Australia AW-00011080 Australia AW-00011081 US AW-00011082 US AW-00011083 US AW-00011084 US AW-00011085 US AW-00011086 US AW-00011087 US AW-00011088 US AW-00011089 US AW-00011090 US AW-00011091 Canada AW-00011092 Australia AW-00011093 Australia AW-00011094 Australia AW-00011095 Australia AW-00011096 Australia AW-00011097 Australia AW-00011098 Australia AW-00011099 Australia AW-00011100 Australia AW-00011101 Australia AW-00011102 Australia AW-00011103 Australia AW-00011104 Australia AW-00011105 Australia AW-00011106 Australia AW-00011107 Australia AW-00011108 Australia AW-00011109 Australia AW-00011110 Australia AW-00011111 Australia AW-00011112 Australia AW-00011113 Australia AW-00011114 Australia AW-00011115 Australia AW-00011116 Australia AW-00011117 Australia AW-00011118 Australia AW-00011119 Australia AW-00011120 Australia AW-00011121 Australia AW-00011122 Australia AW-00011123 Australia AW-00011124 Australia AW-00011125 Australia AW-00011126 Australia AW-00011127 US AW-00011128 US AW-00011129 US AW-00011130 US AW-00011131 Canada AW-00011132 Canada AW-00011133 US AW-00011134 Australia AW-00011135 US AW-00011136 Canada AW-00011137 US AW-00011138 US AW-00011139 Australia AW-00011140 US AW-00011141 US AW-00011142 Canada AW-00011143 US AW-00011144 US AW-00011145 US AW-00011146 Australia AW-00011147 Australia AW-00011148 Australia AW-00011149 Australia AW-00011150 Australia AW-00011151 Australia AW-00011152 US AW-00011153 US AW-00011154 US AW-00011155 US AW-00011156 US AW-00011157 US AW-00011158 US AW-00011159 US AW-00011160 US AW-00011161 US AW-00011162 US AW-00011163 US AW-00011164 US AW-00011165 US AW-00011166 US AW-00011167 US AW-00011168 US AW-00011169 US AW-00011170 US AW-00011171 US AW-00011172 US AW-00011173 US AW-00011174 US AW-00011175 US AW-00011176 Canada AW-00011177 US AW-00011178 US AW-00011179 US AW-00011180 US AW-00011181 US AW-00011182 US AW-00011183 US AW-00011184 US AW-00011185 Canada AW-00011186 US AW-00011187 US AW-00011188 US AW-00011189 US AW-00011190 US AW-00011191 US AW-00011192 US AW-00011193 US AW-00011194 US AW-00011195 US AW-00011196 US AW-00011197 US AW-00011198 US AW-00011199 US AW-00011200 Canada AW-00011201 US AW-00011202 US AW-00011203 Canada AW-00011204 US AW-00011205 US AW-00011206 US AW-00011207 US AW-00011208 US AW-00011209 US AW-00011210 US AW-00011211 Canada AW-00011212 Canada AW-00011213 US AW-00011214 US AW-00011215 Canada 

## Step 1. Inspect join keys (CID vs CRM keys)

Before transforming anything, we quickly check:

- `CID` from ERP (this table)
- `cst_key` from CRM customers

This helps confirm whether formats align or require cleaning.

In [0]:
crm_df = spark.table("bronze.crm_cust_info").select("cst_key")
erp_df = df_raw.select("CID")

crm_df.display()
erp_df.display()

cst_key AW00011000 AW00011001 AW00011002 AW00011003 AW00011004 AW00011005 AW00011006 AW00011007 AW00011008 AW00011009 AW00011010 AW00011011 AW00011012 AW00011013 AW00011014 AW00011015 AW00011016 AW00011017 AW00011018 AW00011019 AW00011020 AW00011021 AW00011022 AW00011023 AW00011024 AW00011025 AW00011026 AW00011027 AW00011028 AW00011029 AW00011030 AW00011031 AW00011032 AW00011033 AW00011034 AW00011035 AW00011036 AW00011037 AW00011038 AW00011039 AW00011040 AW00011041 AW00011042 AW00011043 AW00011044 AW00011045 AW00011046 AW00011047 AW00011048 AW00011049 AW00011050 AW00011051 AW00011052 AW00011053 AW00011054 AW00011055 AW00011056 AW00011057 AW00011058 AW00011059 AW00011060 AW00011061 AW00011062 AW00011063 AW00011064 AW00011065 AW00011066 AW00011067 AW00011068 AW00011069 AW00011070 AW00011071 AW00011072 AW00011073 AW00011074 AW00011075 AW00011076 AW00011077 AW00011078 AW00011079 AW00011080 AW00011081 AW00011082 AW00011083 AW00011084 AW00011085 AW00011086 AW00011087 AW00011088 AW00011089 AW00011090 AW00011091 AW00011092 AW00011093 AW00011094 AW00011095 AW00011096 AW00011097 AW00011098 AW00011099 AW00011100 AW00011101 AW00011102 AW00011103 AW00011104 AW00011105 AW00011106 AW00011107 AW00011108 AW00011109 AW00011110 AW00011111 AW00011112 AW00011113 AW00011114 AW00011115 AW00011116 AW00011117 AW00011118 AW00011119 AW00011120 AW00011121 AW00011122 AW00011123 AW00011124 AW00011125 AW00011126 AW00011127 AW00011128 AW00011129 AW00011130 AW00011131 AW00011132 AW00011133 AW00011134 AW00011135 AW00011136 AW00011137 AW00011138 AW00011139 AW00011140 AW00011141 AW00011142 AW00011143 AW00011144 AW00011145 AW00011146 AW00011147 AW00011148 AW00011149 AW00011150 AW00011151 AW00011152 AW00011153 AW00011154 AW00011155 AW00011156 AW00011157 AW00011158 AW00011159 AW00011160 AW00011161 AW00011162 AW00011163 AW00011164 AW00011165 AW00011166 AW00011167 AW00011168 AW00011169 AW00011170 AW00011171 AW00011172 AW00011173 AW00011174 AW00011175 AW00011176 AW00011177 AW00011178 AW00011179 AW00011180 AW00011181 AW00011182 AW00011183 AW00011184 AW00011185 AW00011186 AW00011187 AW00011188 AW00011189 AW00011190 AW00011191 AW00011192 AW00011193 AW00011194 AW00011195 AW00011196 AW00011197 AW00011198 AW00011199 AW00011200 AW00011201 AW00011202 AW00011203 AW00011204 AW00011205 AW00011206 AW00011207 AW00011208 AW00011209 AW00011210 AW00011211 AW00011212 AW00011213 AW00011214 AW00011215 AW00011216 AW00011217 AW00011218 AW00011219 AW00011220 AW00011221 AW00011222 AW00011223 AW00011224 AW00011225 AW00011226 AW00011227 AW00011228 AW00011229 AW00011230 AW00011231 AW00011232 AW00011233 AW00011234 AW00011235 AW00011236 AW00011237 AW00011238 AW00011239 AW00011240 AW00011241 AW00011242 AW00011243 AW00011244 AW00011245 AW00011246 AW00011247 AW00011248 AW00011249 AW00011250 AW00011251 AW00011252 AW00011253 AW00011254 AW00011255 AW00011256 AW00011257 AW00011258 AW00011259 AW00011260 AW00011261 AW00011262 AW00011263 AW00011264 AW00011265 AW00011266 AW00011267 AW00011268 AW00011269 AW00011270 AW00011271 AW00011272 AW00011273 AW00011274 AW00011275 AW00011276 AW00011277 AW00011278 AW00011279 AW00011280 AW00011281 AW00011282 AW00011283 AW00011284 AW00011285 AW00011286 AW00011287 AW00011288 AW00011289 AW00011290 AW00011291 AW00011292 AW00011293 AW00011294 AW00011295 AW00011296 AW00011297 AW00011298 AW00011299 AW00011300 AW00011301 AW00011302 AW00011303 AW00011304 AW00011305 AW00011306 AW00011307 AW00011308 AW00011309 AW00011310 AW00011311 AW00011312 AW00011313 AW00011314 AW00011315 AW00011316 AW00011317 AW00011318 AW00011319 AW00011320 AW00011321 AW00011322 AW00011323 AW00011324 AW00011325 AW00011326 AW00011327 AW00011328 AW00011329 AW00011330 AW00011331 AW00011332 AW00011333 AW00011334 AW00011335 AW00011336 AW00011337 AW00011338 AW00011339 AW00011340 AW00011341 AW00011342 AW00011343 AW00011344 AW00011345 AW00011346 AW00011347 AW00011348 AW00011349 AW00011350 AW00011351 AW00011352 AW00011353 AW00011354 AW00011355 AW00011356 AW00011357 AW00011358 AW00011359 AW00011360 AW00011361 AW00011362

CID AW-00011000 AW-00011001 AW-00011002 AW-00011003 AW-00011004 AW-00011005 AW-00011006 AW-00011007 AW-00011008 AW-00011009 AW-00011010 AW-00011011 AW-00011012 AW-00011013 AW-00011014 AW-00011015 AW-00011016 AW-00011017 AW-00011018 AW-00011019 AW-00011020 AW-00011021 AW-00011022 AW-00011023 AW-00011024 AW-00011025 AW-00011026 AW-00011027 AW-00011028 AW-00011029 AW-00011030 AW-00011031 AW-00011032 AW-00011033 AW-00011034 AW-00011035 AW-00011036 AW-00011037 AW-00011038 AW-00011039 AW-00011040 AW-00011041 AW-00011042 AW-00011043 AW-00011044 AW-00011045 AW-00011046 AW-00011047 AW-00011048 AW-00011049 AW-00011050 AW-00011051 AW-00011052 AW-00011053 AW-00011054 AW-00011055 AW-00011056 AW-00011057 AW-00011058 AW-00011059 AW-00011060 AW-00011061 AW-00011062 AW-00011063 AW-00011064 AW-00011065 AW-00011066 AW-00011067 AW-00011068 AW-00011069 AW-00011070 AW-00011071 AW-00011072 AW-00011073 AW-00011074 AW-00011075 AW-00011076 AW-00011077 AW-00011078 AW-00011079 AW-00011080 AW-00011081 AW-00011082 AW-00011083 AW-00011084 AW-00011085 AW-00011086 AW-00011087 AW-00011088 AW-00011089 AW-00011090 AW-00011091 AW-00011092 AW-00011093 AW-00011094 AW-00011095 AW-00011096 AW-00011097 AW-00011098 AW-00011099 AW-00011100 AW-00011101 AW-00011102 AW-00011103 AW-00011104 AW-00011105 AW-00011106 AW-00011107 AW-00011108 AW-00011109 AW-00011110 AW-00011111 AW-00011112 AW-00011113 AW-00011114 AW-00011115 AW-00011116 AW-00011117 AW-00011118 AW-00011119 AW-00011120 AW-00011121 AW-00011122 AW-00011123 AW-00011124 AW-00011125 AW-00011126 AW-00011127 AW-00011128 AW-00011129 AW-00011130 AW-00011131 AW-00011132 AW-00011133 AW-00011134 AW-00011135 AW-00011136 AW-00011137 AW-00011138 AW-00011139 AW-00011140 AW-00011141 AW-00011142 AW-00011143 AW-00011144 AW-00011145 AW-00011146 AW-00011147 AW-00011148 AW-00011149 AW-00011150 AW-00011151 AW-00011152 AW-00011153 AW-00011154 AW-00011155 AW-00011156 AW-00011157 AW-00011158 AW-00011159 AW-00011160 AW-00011161 AW-00011162 AW-00011163 AW-00011164 AW-00011165 AW-00011166 AW-00011167 AW-00011168 AW-00011169 AW-00011170 AW-00011171 AW-00011172 AW-00011173 AW-00011174 AW-00011175 AW-00011176 AW-00011177 AW-00011178 AW-00011179 AW-00011180 AW-00011181 AW-00011182 AW-00011183 AW-00011184 AW-00011185 AW-00011186 AW-00011187 AW-00011188 AW-00011189 AW-00011190 AW-00011191 AW-00011192 AW-00011193 AW-00011194 AW-00011195 AW-00011196 AW-00011197 AW-00011198 AW-00011199 AW-00011200 AW-00011201 AW-00011202 AW-00011203 AW-00011204 AW-00011205 AW-00011206 AW-00011207 AW-00011208 AW-00011209 AW-00011210 AW-00011211 AW-00011212 AW-00011213 AW-00011214 AW-00011215 AW-00011216 AW-00011217 AW-00011218 AW-00011219 AW-00011220 AW-00011221 AW-00011222 AW-00011223 AW-00011224 AW-00011225 AW-00011226 AW-00011227 AW-00011228 AW-00011229 AW-00011230 AW-00011231 AW-00011232 AW-00011233 AW-00011234 AW-00011235 AW-00011236 AW-00011237 AW-00011238 AW-00011239 AW-00011240 AW-00011241 AW-00011242 AW-00011243 AW-00011244 AW-00011245 AW-00011246 AW-00011247 AW-00011248 AW-00011249 AW-00011250 AW-00011251 AW-00011252 AW-00011253 AW-00011254 AW-00011255 AW-00011256 AW-00011257 AW-00011258 AW-00011259 AW-00011260 AW-00011261 AW-00011262 AW-00011263 AW-00011264 AW-00011265 AW-00011266 AW-00011267 AW-00011268 AW-00011269 AW-00011270 AW-00011271 AW-00011272 AW-00011273 AW-00011274 AW-00011275 AW-00011276 AW-00011277 AW-00011278 AW-00011279 AW-00011280 AW-00011281 AW-00011282 AW-00011283 AW-00011284 AW-00011285 AW-00011286 AW-00011287 AW-00011288 AW-00011289 AW-00011290 AW-00011291 AW-00011292 AW-00011293 AW-00011294 AW-00011295 AW-00011296 AW-00011297 AW-00011298 AW-00011299 AW-00011300 AW-00011301 AW-00011302 AW-00011303 AW-00011304 AW-00011305 AW-00011306 AW-00011307 AW-00011308 AW-00011309 AW-00011310 AW-00011311 AW-00011312 AW-00011313 AW-00011314 AW-00011315 AW-00011316 AW-00011317 AW-00011318 AW-00011319 AW-00011320 AW-00011321 AW-00011322 AW-00011323 AW-00011324 AW-00011325 AW-00011326 AW-00011327 AW-00011328 AW-00011329 AW-00011330 AW-00011331 AW-00011332 

## Step 2. Clean CID values

Issue:
Some `CID` values contain hyphens (`-`), which can break joins or create mismatches.

Action:
Remove hyphens only.  
No other transformations are applied.

In [0]:
df_clean = df_raw.withColumn(
    "CID_clean",
    F.regexp_replace("CID", "-", "")
)

df_clean.select("CID", "CID_clean").display()

CID CID_clean AW-00011000 AW00011000 AW-00011001 AW00011001 AW-00011002 AW00011002 AW-00011003 AW00011003 AW-00011004 AW00011004 AW-00011005 AW00011005 AW-00011006 AW00011006 AW-00011007 AW00011007 AW-00011008 AW00011008 AW-00011009 AW00011009 AW-00011010 AW00011010 AW-00011011 AW00011011 AW-00011012 AW00011012 AW-00011013 AW00011013 AW-00011014 AW00011014 AW-00011015 AW00011015 AW-00011016 AW00011016 AW-00011017 AW00011017 AW-00011018 AW00011018 AW-00011019 AW00011019 AW-00011020 AW00011020 AW-00011021 AW00011021 AW-00011022 AW00011022 AW-00011023 AW00011023 AW-00011024 AW00011024 AW-00011025 AW00011025 AW-00011026 AW00011026 AW-00011027 AW00011027 AW-00011028 AW00011028 AW-00011029 AW00011029 AW-00011030 AW00011030 AW-00011031 AW00011031 AW-00011032 AW00011032 AW-00011033 AW00011033 AW-00011034 AW00011034 AW-00011035 AW00011035 AW-00011036 AW00011036 AW-00011037 AW00011037 AW-00011038 AW00011038 AW-00011039 AW00011039 AW-00011040 AW00011040 AW-00011041 AW00011041 AW-00011042 AW00011042 AW-00011043 AW00011043 AW-00011044 AW00011044 AW-00011045 AW00011045 AW-00011046 AW00011046 AW-00011047 AW00011047 AW-00011048 AW00011048 AW-00011049 AW00011049 AW-00011050 AW00011050 AW-00011051 AW00011051 AW-00011052 AW00011052 AW-00011053 AW00011053 AW-00011054 AW00011054 AW-00011055 AW00011055 AW-00011056 AW00011056 AW-00011057 AW00011057 AW-00011058 AW00011058 AW-00011059 AW00011059 AW-00011060 AW00011060 AW-00011061 AW00011061 AW-00011062 AW00011062 AW-00011063 AW00011063 AW-00011064 AW00011064 AW-00011065 AW00011065 AW-00011066 AW00011066 AW-00011067 AW00011067 AW-00011068 AW00011068 AW-00011069 AW00011069 AW-00011070 AW00011070 AW-00011071 AW00011071 AW-00011072 AW00011072 AW-00011073 AW00011073 AW-00011074 AW00011074 AW-00011075 AW00011075 AW-00011076 AW00011076 AW-00011077 AW00011077 AW-00011078 AW00011078 AW-00011079 AW00011079 AW-00011080 AW00011080 AW-00011081 AW00011081 AW-00011082 AW00011082 AW-00011083 AW00011083 AW-00011084 AW00011084 AW-00011085 AW00011085 AW-00011086 AW00011086 AW-00011087 AW00011087 AW-00011088 AW00011088 AW-00011089 AW00011089 AW-00011090 AW00011090 AW-00011091 AW00011091 AW-00011092 AW00011092 AW-00011093 AW00011093 AW-00011094 AW00011094 AW-00011095 AW00011095 AW-00011096 AW00011096 AW-00011097 AW00011097 AW-00011098 AW00011098 AW-00011099 AW00011099 AW-00011100 AW00011100 AW-00011101 AW00011101 AW-00011102 AW00011102 AW-00011103 AW00011103 AW-00011104 AW00011104 AW-00011105 AW00011105 AW-00011106 AW00011106 AW-00011107 AW00011107 AW-00011108 AW00011108 AW-00011109 AW00011109 AW-00011110 AW00011110 AW-00011111 AW00011111 AW-00011112 AW00011112 AW-00011113 AW00011113 AW-00011114 AW00011114 AW-00011115 AW00011115 AW-00011116 AW00011116 AW-00011117 AW00011117 AW-00011118 AW00011118 AW-00011119 AW00011119 AW-00011120 AW00011120 AW-00011121 AW00011121 AW-00011122 AW00011122 AW-00011123 AW00011123 AW-00011124 AW00011124 AW-00011125 AW00011125 AW-00011126 AW00011126 AW-00011127 AW00011127 AW-00011128 AW00011128 AW-00011129 AW00011129 AW-00011130 AW00011130 AW-00011131 AW00011131 AW-00011132 AW00011132 AW-00011133 AW00011133 AW-00011134 AW00011134 AW-00011135 AW00011135 AW-00011136 AW00011136 AW-00011137 AW00011137 AW-00011138 AW00011138 AW-00011139 AW00011139 AW-00011140 AW00011140 AW-00011141 AW00011141 AW-00011142 AW00011142 AW-00011143 AW00011143 AW-00011144 AW00011144 AW-00011145 AW00011145 AW-00011146 AW00011146 AW-00011147 AW00011147 AW-00011148 AW00011148 AW-00011149 AW00011149 AW-00011150 AW00011150 AW-00011151 AW00011151 AW-00011152 AW00011152 AW-00011153 AW00011153 AW-00011154 AW00011154 AW-00011155 AW00011155 AW-00011156 AW00011156 AW-00011157 AW00011157 AW-00011158 AW00011158 AW-00011159 AW00011159 AW-00011160 AW00011160 AW-00011161 AW00011161 AW-00011162 AW00011162 AW-00011163 AW00011163 AW-00011164 AW00011164 AW-00011165 AW00011165 AW-00011166 AW00011166 AW-00011167 AW00011167 AW-00011168 AW00011168 AW-00011169 AW00011169 AW-00011170 AW00011170 AW-00011171 AW00011171 AW-00011172 AW00011172 AW-0001

## Step 3. Explore country values

We check distinct `CNTRY` values to identify:
- spelling differences
- abbreviations
- unexpected or invalid entries

This informs the normalization logic.

In [0]:
df_raw.select("CNTRY").distinct().display()

CNTRY Australia US Canada DE United Kingdom France USA Germany United States null

## Step 4. Normalize country names

We standardize country labels to a consistent format:

Mappings:
- US / USA / UNITED STATES → United States
- DE / GERMANY → Germany
- UNITED KINGDOM / AUSTRALIA / CANADA / FRANCE → kept as-is
- everything else → `n/a`

This ensures consistent grouping and reporting.

In [0]:
df_normalized = (
    df_clean
    .withColumn("CNTRY_trim", F.upper(F.trim("CNTRY")))
    .withColumn(
        "CNTRY_clean",
        F.when(F.col("CNTRY_trim").isin("US","USA","UNITED STATES"), "United States")
         .when(F.col("CNTRY_trim").isin("GERMANY","DE"), "Germany")
         .when(F.col("CNTRY_trim").isin("UNITED KINGDOM","AUSTRALIA","CANADA","FRANCE"), F.col("CNTRY"))
         .otherwise("n/a")
    )
)

df_normalized.select("CNTRY", "CNTRY_clean").display()

CNTRY CNTRY_clean Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia US United States US United States US United States US United States US United States Australia Australia Australia Australia Canada Canada Canada Canada US United States US United States US United States US United States Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia US United States Canada Canada Australia Australia Australia Australia US United States US United States US United States US United States Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia US United States Australia Australia Australia Australia Australia Australia US United States Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia US United States US United States US United States US United States US United States US United States Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Canada Canada Australia Australia Australia Australia US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States Canada Canada Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia US United States US United States US United States US United States Canada Canada Canada Canada US United States Australia Australia US United States Canada Canada US United States US United States Australia Australia US United States US United States Canada Canada US United States US United States US United States Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia Australia US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States Canada Canada US United States US United States US United States US United States US United States US United States US United States US United States Canada Canada US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States US United States Canada Canada US United States US United States Canada Canada US United States US United States US United States US United States US United States US United States US United States Canada Canada Canada Canada US United States US United States Canada Canada US United States US United States US United States US United Sta

## Step 5. Create final Silver dataset

The Silver table keeps only:
- cleaned customer ID
- normalized country

All temporary helper columns are removed.

This dataset is now:
- join-safe
- standardized
- analytics-ready

In [0]:
silver_df = (
    df_normalized
    .select(
        F.col("CID_clean").alias("CID"),
        F.col("CNTRY_clean").alias("CNTRY")
    )
)
silver_df = silver_df.select("*",F.current_timestamp().alias("dwh_create_date"))
silver_df.display()

CID CNTRY dwh_create_date AW00011000 Australia 2026-02-08T06:28:26.968Z AW00011001 Australia 2026-02-08T06:28:26.968Z AW00011002 Australia 2026-02-08T06:28:26.968Z AW00011003 Australia 2026-02-08T06:28:26.968Z AW00011004 Australia 2026-02-08T06:28:26.968Z AW00011005 Australia 2026-02-08T06:28:26.968Z AW00011006 Australia 2026-02-08T06:28:26.968Z AW00011007 Australia 2026-02-08T06:28:26.968Z AW00011008 Australia 2026-02-08T06:28:26.968Z AW00011009 Australia 2026-02-08T06:28:26.968Z AW00011010 Australia 2026-02-08T06:28:26.968Z AW00011011 Australia 2026-02-08T06:28:26.968Z AW00011012 United States 2026-02-08T06:28:26.968Z AW00011013 United States 2026-02-08T06:28:26.968Z AW00011014 United States 2026-02-08T06:28:26.968Z AW00011015 United States 2026-02-08T06:28:26.968Z AW00011016 United States 2026-02-08T06:28:26.968Z AW00011017 Australia 2026-02-08T06:28:26.968Z AW00011018 Australia 2026-02-08T06:28:26.968Z AW00011019 Canada 2026-02-08T06:28:26.968Z AW00011020 Canada 2026-02-08T06:28:26.968Z AW00011021 United States 2026-02-08T06:28:26.968Z AW00011022 United States 2026-02-08T06:28:26.968Z AW00011023 United States 2026-02-08T06:28:26.968Z AW00011024 United States 2026-02-08T06:28:26.968Z AW00011025 Australia 2026-02-08T06:28:26.968Z AW00011026 Australia 2026-02-08T06:28:26.968Z AW00011027 Australia 2026-02-08T06:28:26.968Z AW00011028 Australia 2026-02-08T06:28:26.968Z AW00011029 Australia 2026-02-08T06:28:26.968Z AW00011030 Australia 2026-02-08T06:28:26.968Z AW00011031 Australia 2026-02-08T06:28:26.968Z AW00011032 Australia 2026-02-08T06:28:26.968Z AW00011033 Australia 2026-02-08T06:28:26.968Z AW00011034 Australia 2026-02-08T06:28:26.968Z AW00011035 Australia 2026-02-08T06:28:26.968Z AW00011036 United States 2026-02-08T06:28:26.968Z AW00011037 Canada 2026-02-08T06:28:26.968Z AW00011038 Australia 2026-02-08T06:28:26.968Z AW00011039 Australia 2026-02-08T06:28:26.968Z AW00011040 United States 2026-02-08T06:28:26.968Z AW00011041 United States 2026-02-08T06:28:26.968Z AW00011042 United States 2026-02-08T06:28:26.968Z AW00011043 United States 2026-02-08T06:28:26.968Z AW00011044 Australia 2026-02-08T06:28:26.968Z AW00011045 Australia 2026-02-08T06:28:26.968Z AW00011046 Australia 2026-02-08T06:28:26.968Z AW00011047 Australia 2026-02-08T06:28:26.968Z AW00011048 Australia 2026-02-08T06:28:26.968Z AW00011049 United States 2026-02-08T06:28:26.968Z AW00011050 Australia 2026-02-08T06:28:26.968Z AW00011051 Australia 2026-02-08T06:28:26.968Z AW00011052 Australia 2026-02-08T06:28:26.968Z AW00011053 United States 2026-02-08T06:28:26.968Z AW00011054 Australia 2026-02-08T06:28:26.968Z AW00011055 Australia 2026-02-08T06:28:26.968Z AW00011056 Australia 2026-02-08T06:28:26.968Z AW00011057 Australia 2026-02-08T06:28:26.968Z AW00011058 Australia 2026-02-08T06:28:26.968Z AW00011059 Australia 2026-02-08T06:28:26.968Z AW00011060 Australia 2026-02-08T06:28:26.968Z AW00011061 Australia 2026-02-08T06:28:26.968Z AW00011062 United States 2026-02-08T06:28:26.968Z AW00011063 United States 2026-02-08T06:28:26.968Z AW00011064 United States 2026-02-08T06:28:26.968Z AW00011065 United States 2026-02-08T06:28:26.968Z AW00011066 United States 2026-02-08T06:28:26.968Z AW00011067 United States 2026-02-08T06:28:26.968Z AW00011068 Australia 2026-02-08T06:28:26.968Z AW00011069 Australia 2026-02-08T06:28:26.968Z AW00011070 Australia 2026-02-08T06:28:26.968Z AW00011071 Australia 2026-02-08T06:28:26.968Z AW00011072 Australia 2026-02-08T06:28:26.968Z AW00011073 Australia 2026-02-08T06:28:26.968Z AW00011074 Australia 2026-02-08T06:28:26.968Z AW00011075 Australia 2026-02-08T06:28:26.968Z AW00011076 Australia 2026-02-08T06:28:26.968Z AW00011077 Australia 2026-02-08T06:28:26.968Z AW00011078 Canada 2026-02-08T06:28:26.968Z AW00011079 Australia 2026-02-08T06:28:26.968Z AW00011080 Australia 2026-02-08T06:28:26.968Z AW00011081 United States 2026-02-08T06:28:26.968Z AW00011082 United States 2026-02-08T06:28:26.968Z AW00011083 United States 2026-02-08T06:28:26.968Z AW00011084 United Stat

## Step 6. Save as Silver Delta table

Persist the cleaned dataset to the Silver layer as a Delta table.
This becomes the curated source for downstream transformations and reporting.

In [0]:
(
    silver_df
    .write
    .format("delta")
    .mode("overwrite")
    .saveAsTable("datawarehouse.silver.erp_loc_a101")
)